In [2]:
# filter crops
import glob
import matplotlib.pyplot as plt
import numpy as np
import os
import shutil
from tqdm import tqdm
import cv2

filter_dir = '/files/datasets/lacmus-ds/ladd_crop/ds_filtred/train/Backgruond'

files = glob.glob('/files/datasets/lacmus-ds/ladd_crop/ds_filtred/train/Background/*')
print(len(files))

files = list(np.random.choice(files, size=17))
imgs = []

for f in files:
    imgs.append(cv2.imread(f))
    
def plot_figures(figures, nrows = 4, ncols=4):
    """Plot a dictionary of figures.

    Parameters
    ----------
    figures : <title, figure> dictionary
    ncols : number of columns of subplots wanted in the display
    nrows : number of rows of subplots wanted in the figure
    """
    fig=plt.figure(figsize=(200, 200))
    columns = ncols
    rows = nrows
    for i in range(1, len(figures)):
        img = figures[i-1]
        fig.add_subplot(rows, columns, i)
        plt.imshow(img)
    plt.show()
    
plot_figures(imgs)

8904


In [22]:
count = 0
for idx in range(1, 64):
    count = count + 1
    if count < 32 and idx < 64 - 1:
        continue
    else:
        print(f'predict on: {idx-count} - {idx}')
        count = 0

predict on: 0 - 32
predict on: 32 - 63


In [30]:
import os
import sys

import argparse

from pathlib import Path

import tensorflow as tf
from tensorflow.python.framework import graph_util
from tensorflow.python.framework import graph_io

from keras import backend as K
from keras.models import load_model


def setKerasOptions():
    K._LEARNING_PHASE = tf.constant(0)
    K.set_learning_phase(False)
    K.set_learning_phase(0)
    K.set_image_data_format('channels_last')


def getInputParameters():
    parser = argparse.ArgumentParser()
    parser.add_argument('--input_model', '-m', required=True, type=str, help='Path to Keras model.')
    parser.add_argument('--num_outputs', '-no', required=False, type=int, help='Number of outputs. 1 by default.', default=1)

    return parser


def export_keras_to_tf(input_model, output_model, num_output):
    print('Loading Keras model: ', input_model)

    keras_model = load_model(input_model)

    print(keras_model.summary())

    predictions = [None] * num_output
    predrediction_node_names = [None] * num_output

    for i in range(num_output):
        predrediction_node_names[i] = 'output_node' + str(i)
        predictions[i] = tf.identity(keras_model.outputs[i], name=predrediction_node_names[i])

    sess = K.get_session()

    constant_graph = graph_util.convert_variables_to_constants(sess, sess.graph.as_graph_def(), predrediction_node_names)
    infer_graph = graph_util.remove_training_nodes(constant_graph) 

    graph_io.write_graph(infer_graph, '.', output_model, as_text=False)

In [32]:
import tensorflow as tf
from keras.models import Model
import keras
from keras.applications.resnet_v2 import ResNet50V2, preprocess_input
from keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout, InputLayer
from keras.models import Sequential
from keras import optimizers
K.set_learning_phase(0)

WIDTH = 224
HEIGHT = 224
BATCH_SIZE = 32

restnet50 = ResNet50V2(include_top=True, weights='imagenet', input_shape=(HEIGHT,WIDTH,3))

model = restnet50.output
model = Dense(512, activation='relu')(model)
model = Dense(1, activation='sigmoid')(model)

model = Model(inputs=restnet50.input, outputs=model)

model.load_weights("model.0.98-0.09.h5")
model.save("model.h5")

export_keras_to_tf("model.h5", "model_tf.pb", 1)

Loading Keras model:  model.h5


/home/gosha20777/.local/lib/python3.7/site-packages/keras/engine/saving.py:341: UserWarning: No training configuration found in save file: the model was *not* compiled. Compile it manually.
  warnings.warn('No training configuration found in save file: '


Model: "model_5"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_5 (InputLayer)            (None, 224, 224, 3)  0                                            
__________________________________________________________________________________________________
conv1_pad (ZeroPadding2D)       (None, 230, 230, 3)  0           input_5[0][0]                    
__________________________________________________________________________________________________
conv1_conv (Conv2D)             (None, 112, 112, 64) 9472        conv1_pad[0][0]                  
__________________________________________________________________________________________________
pool1_pad (ZeroPadding2D)       (None, 114, 114, 64) 0           conv1_conv[0][0]                 
____________________________________________________________________________________________

ValueError: Cannot find the variable that is an input to the ReadVariableOp.

In [33]:
import tensorflow as tf
from tensorflow.python.framework import graph_io
from tensorflow.keras.models import load_model


# Clear any previous session.
tf.keras.backend.clear_session()

save_pb_dir = './'
model_fname = './model.h5'
def freeze_graph(graph, session, output, save_pb_dir='.', save_pb_name='frozen_model.pb', save_pb_as_text=False):
    with graph.as_default():
        graphdef_inf = tf.graph_util.remove_training_nodes(graph.as_graph_def())
        graphdef_frozen = tf.graph_util.convert_variables_to_constants(session, graphdef_inf, output)
        graph_io.write_graph(graphdef_frozen, save_pb_dir, save_pb_name, as_text=save_pb_as_text)
        return graphdef_frozen

# This line must be executed before loading Keras model.
tf.keras.backend.set_learning_phase(0) 

model = load_model(model_fname)

session = tf.keras.backend.get_session()

INPUT_NODE = [t.op.name for t in model.inputs]
OUTPUT_NODE = [t.op.name for t in model.outputs]
print(INPUT_NODE, OUTPUT_NODE)
frozen_graph = freeze_graph(session.graph, session, [out.op.name for out in model.outputs], save_pb_dir=save_pb_dir)

['input_5'] ['dense_10/Sigmoid']
Instructions for updating:
Use `tf.compat.v1.graph_util.remove_training_nodes`
INFO:tensorflow:Froze 276 variables.
INFO:tensorflow:Converted 276 variables to const ops.
